## Overview
This notebook calibrates the high-frequency output flatness of a signal generator. It works by:
1.  Connecting to the signal generator and an oscilloscope via VISA (TCPIP).
2.  Measuring the generator's actual RMS output voltage across specified frequency points for different amplitude ranges using the oscilloscope.
3.  Reading the generator's existing high-frequency flatness calibration data (`cal_hfflat*.hex` files).
4.  Calculating correction factors based on the difference between the measured response and the ideal flat response.
5.  Applying these corrections to the existing calibration data, focusing on higher frequency points within each range.
6.  Saving the updated calibration data into new `.hex` files.
7.  Providing commands to upload the new calibration files to the generator using ADB (Android Debug Bridge).

## Hardware Setup
*   Connect the Signal Generator and Oscilloscope to the network.
*   Connect the Signal Generator's output channel (CH1 or CH2) to the Oscilloscope's input channel (specified in `OSC_MEAS_CHAN`).
*   Use a high-quality 50 Ohm coaxial cable.
*   **Important:** Ensure the Oscilloscope's input channel impedance is set to **50 Ohms**.
*   Enable ADB debugging on the Signal Generator (likely via network).

## 1. Configuration
Adjust the parameters below to match your setup.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pyvisa
import time
import os
import pathlib  # Optional, can use os.path instead

# --- Instrument & Connection Settings ---
GEN_IP = "192.168.138.178"  # IP Address of the Signal Generator
OSC_IP = "192.168.138.244"  # IP Address of the Oscilloscope
ADB_DEVICE_ID = (
    "192.168.138.178:55555"  # ADB identifier for the generator (IP:Port or Serial)
)

# --- File Paths ---
# Directory where original .hex files are located and where measurement/modified files will be saved.
# Use raw string (r'...') or forward slashes ('/') for paths.
DATA_DIR = r"C:\Users\xxx\dgpro_calibration_data"  # CHANGE THIS PATH

# Ensure the data directory exists
pathlib.Path(DATA_DIR).mkdir(
    parents=True, exist_ok=True
)  # Create dir if it doesn't exist

# Original and modified calibration filenames (don't change filename structure unless necessary)
ORIGINAL_HEX_FILES = {1: "cal_hfflat1.hex", 2: "cal_hfflat2.hex"}
MODIFIED_HEX_FILES = {1: "cal_hfflat1_mod.hex", 2: "cal_hfflat2_mod.hex"}
MEASUREMENT_FILE_TEMPLATE = (
    "ch{channel}-rng{range_idx}-measurement.npz"  # Template for saving measurements
)

# --- SCPI Commands ---
# Adjust these if your instruments use different commands
GEN_IDN_CMD = "*IDN?"
OSC_IDN_CMD = "*IDN?"
GEN_SET_VOLT_CMD = ":SOURce{ch}:VOLTage:AMPLitude {volt:.7e} VPP"  # Set Vpp
GEN_SET_FREQ_CMD = ":SOURce{ch}:FREQuency {freq:.4e}"  # Set Frequency in Hz
# *** IMPORTANT: Change this for your specific oscilloscope model! ***
# Example for many Siglent scopes: Query RMS voltage on Channel 1 -> 'C1:PAVA? RMS'
# Example from original code (might be Rigol): ':MEAS:ITEM? VRMS,CHAN1'
OSC_MEAS_CMD = "C1:PAVA? RMS"  # Placeholder - REPLACE WITH YOUR SCOPE'S COMMAND
OSC_MEAS_CHAN = "1"  # Oscilloscope channel connected to the generator output (used if needed in OSC_MEAS_CMD)

# --- Calibration Settings ---
CHANNELS_TO_CALIBRATE = [
    1,
    2,
]  # List of generator channels to calibrate (e.g., [1], [2], or [1, 2])
SETTLE_TIME_VOLT = 3.0  # Seconds to wait after setting voltage
SETTLE_TIME_FREQ = 0.7  # Seconds to wait after setting frequency

# Define the calibration ranges, frequencies, and corresponding indices in the .hex file.
# Each range dictionary needs:
#   'voltage': Target Vpp for measurements in this range.
#   'frequencies_uHz': List/array of frequencies in microHertz (uHz).
#   'hex_start_idx': Starting index (1-based) in the hex file for this range's data.
#   'hex_end_idx': Ending index (inclusive) in the hex file for this range's data.
#   'points_to_modify': Number of *highest frequency points* within this range to apply correction to.

# Frequencies are defined once and reused (converted from uHz to Hz later)
# Note: The original code reversed the lists, meaning measurements went from high to low freq. Preserving that.
#       Also, the number of points varied slightly per range.
FREQ_LIST_RANGE_1_3_uHz = np.array(
    list(
        reversed(
            [
                200000000000000,
                175000000000000,
                150000000000000,
                120000000000000,
                100000000000000,
                90000000000000,
                80000000000000,
                70000000000000,
                60000000000000,
                50000000000000,
                40000000000000,
                30000000000000,
                20000000000000,
                10000000000000,
                8000000000000,
                6000000000000,
                4000000000000,
                2000000000000,
                1000000000000,
                900000000000,
                800000000000,
                700000000000,
                600000000000,
                500000000000,
                400000000000,
                300000000000,
                200000000000,
            ]
        )
    )
)  # 27 points: 200kHz to 200MHz

FREQ_LIST_RANGE_2_uHz = np.array(
    list(
        reversed(
            [
                100000000000000,
                90000000000000,
                80000000000000,
                70000000000000,
                60000000000000,
                50000000000000,
                40000000000000,
                30000000000000,
                20000000000000,
                10000000000000,
                8000000000000,
                6000000000000,
                4000000000000,
                2000000000000,
                1000000000000,
                900000000000,
                800000000000,
                700000000000,
                600000000000,
                500000000000,
                400000000000,
                300000000000,
                200000000000,
            ]
        )
    )
)  # 23 points: 200kHz to 100MHz

# Structure defining the ranges for calibration
# Indices match boundaries observed in original code (1-27, 28-50, 51-77)
# Note: Vpp values from original code comments/calculations are used.
CAL_RANGES = [
    {  # Range 1 (corresponds to original `rng1`)
        "voltage": 1.2649111,  # Vpp
        "frequencies_uHz": FREQ_LIST_RANGE_1_3_uHz,
        "hex_start_idx": 1,
        "hex_end_idx": 27,
        "points_to_modify": 12,
    },
    {  # Range 2 (corresponds to original `rng2`)
        "voltage": 5.0,  # Vpp
        "frequencies_uHz": FREQ_LIST_RANGE_2_uHz,
        "hex_start_idx": 28,
        "hex_end_idx": 50,  # 23 points total
        "points_to_modify": 12,
    },
    {  # Range 3 (corresponds to original `rng3` - 0dBm into 50 Ohm)
        "voltage": 0.6324556,  # Vpp (approx 0 dBm)
        "frequencies_uHz": FREQ_LIST_RANGE_1_3_uHz,
        "hex_start_idx": 51,
        "hex_end_idx": 77,
        "points_to_modify": 12,
    },
]

# Hex file properties
HEX_DATA_TYPE = "<f8"  # Little-endian 64-bit float
HEX_POINTS_PER_CHANNEL = 78  # Total points = 624 bytes / 8 bytes/point

# --- Plotting Defaults ---
plt.rcParams["figure.figsize"] = (10, 6)  # Default figure size

print("Configuration loaded.")
print(f"Data Directory: {DATA_DIR}")
print(f"Generator IP: {GEN_IP}, Oscilloscope IP: {OSC_IP}")
print(f"Calibrating Channels: {CHANNELS_TO_CALIBRATE}")
print(f"Oscilloscope Measurement Command: {OSC_MEAS_CMD}")

## 2. Helper Functions

In [ ]:
def connect_instruments(gen_ip, osc_ip):
    """Connects to Generator and Oscilloscope using pyvisa."""
    gen = None
    osc = None
    try:
        print("Connecting to instruments...")
        rm = pyvisa.ResourceManager()
        gen_addr = f"TCPIP0::{gen_ip}::INSTR"
        osc_addr = f"TCPIP0::{osc_ip}::INSTR"

        gen = rm.open_resource(gen_addr)
        gen.timeout = 10000  # ms
        gen.read_termination = "\n"
        gen.write_termination = "\n"
        print(f"Generator Connected: {gen.query(GEN_IDN_CMD).strip()}")

        osc = rm.open_resource(osc_addr)
        osc.timeout = 10000  # ms
        osc.read_termination = "\n"
        osc.write_termination = "\n"
        print(f"Oscilloscope Connected: {osc.query(OSC_IDN_CMD).strip()}")
        print("-" * 30)
        return gen, osc
    except pyvisa.errors.VisaIOError as e:
        print(f"VISA Error connecting to instruments: {e}")
        if gen:
            gen.close()
        if osc:
            osc.close()
        return None, None
    except Exception as e:
        print(f"An unexpected error occurred during connection: {e}")
        if gen:
            gen.close()
        if osc:
            osc.close()
        return None, None


def measure_flatness(gen, osc, channel, voltage_vpp, frequencies_hz, osc_meas_cmd):
    """Sets generator and measures RMS voltage using the oscilloscope."""
    measured_amps_rms = np.zeros_like(frequencies_hz, dtype=float)

    print(f"Starting measurement: CH{channel}, Voltage={voltage_vpp:.4f} Vpp")

    # Set initial voltage
    cmd = GEN_SET_VOLT_CMD.format(ch=channel, volt=voltage_vpp)
    # print(f"Sending to Gen: {cmd}") # Uncomment for debugging
    gen.write(cmd)
    time.sleep(SETTLE_TIME_VOLT)

    # Set initial frequency (first in the list)
    cmd = GEN_SET_FREQ_CMD.format(ch=channel, freq=frequencies_hz[0])
    # print(f"Sending to Gen: {cmd}") # Uncomment for debugging
    gen.write(cmd)
    time.sleep(SETTLE_TIME_FREQ)  # Allow settling before first measurement

    # Loop through frequencies
    for i, freq_hz in enumerate(frequencies_hz):
        cmd = GEN_SET_FREQ_CMD.format(ch=channel, freq=freq_hz)
        # print(f"Sending to Gen: {cmd}") # Uncomment for debugging
        gen.write(cmd)
        time.sleep(SETTLE_TIME_FREQ)

        # Measure RMS Voltage
        try:
            # Adapt query based on expected Siglent format (value first, then unit maybe)
            # Or based on original format (just the value)
            query_cmd = osc_meas_cmd.replace(
                "C1", f"C{OSC_MEAS_CHAN}"
            )  # Replace channel if needed
            # print(f"Querying Scope: {query_cmd}") # Uncomment for debugging
            response = osc.query(query_cmd).strip()

            # Attempt to extract float - adjust parsing if needed based on scope response
            # e.g., if it returns "1.234 VRMS", split and take first part
            try:
                measured_vrms = float(response.split()[0])  # Example parsing
            except ValueError:
                measured_vrms = float(
                    response
                )  # Assume direct float response if split fails

            measured_amps_rms[i] = measured_vrms
            print(
                f"  Freq: {freq_hz / 1e6:.3f} MHz, Measured VRMS: {measured_vrms:.6f} V"
            )
        except pyvisa.errors.VisaIOError as e:
            print(f"VISA Error during measurement at {freq_hz / 1e6:.3f} MHz: {e}")
            measured_amps_rms[i] = np.nan  # Mark as invalid
        except Exception as e:
            print(
                f"Unexpected error during measurement at {freq_hz / 1e6:.3f} MHz: {e}"
            )
            measured_amps_rms[i] = np.nan  # Mark as invalid

    print(f"Measurement finished for CH{channel}, Voltage={voltage_vpp:.4f} Vpp.")
    print("-" * 30)
    return frequencies_hz, measured_amps_rms


def calculate_and_update_cal(
    original_hex_path, all_measurements, cal_ranges, hex_data_type, output_hex_path
):
    """Calculates new calibration factors and writes the modified .hex file."""
    print(f"Processing calibration for: {output_hex_path}")

    # 1. Read original calibration data
    try:
        with open(original_hex_path, "rb") as fh:
            original_cal_data = np.fromfile(fh, dtype=hex_data_type)
        print(f"Read {len(original_cal_data)} points from {original_hex_path}")
        if len(original_cal_data) != HEX_POINTS_PER_CHANNEL:
            print(
                f"Warning: Expected {HEX_POINTS_PER_CHANNEL} points, found {len(original_cal_data)}."
            )
            # Decide how to handle: error out, proceed with caution?
            # For now, proceed cautiously. Add error handling if needed.
            # return False
    except FileNotFoundError:
        print(f"Error: Original calibration file not found: {original_hex_path}")
        return False
    except Exception as e:
        print(f"Error reading {original_hex_path}: {e}")
        return False

    modified_cal_data = original_cal_data.copy()
    plt.figure()  # Create a figure for plotting results for this channel

    # 2. Process each calibration range
    for i, cal_range in enumerate(cal_ranges):
        range_idx = i + 1  # 1-based index for user feedback/filenames
        print(f" Applying corrections for Range {range_idx}...")

        # Find the measurement data for this range
        measurement_data = all_measurements.get(range_idx)
        if measurement_data is None:
            print(f" Error: Measurement data for range {range_idx} not found.")
            continue  # Skip this range

        measured_freqs = measurement_data["frequencies_hz"]
        measured_amps = measurement_data["measured_amps_rms"]

        # Basic check for NaNs or zeros which would break calculation
        if np.isnan(measured_amps).any() or measured_amps[0] == 0:
            print(
                f" Warning: Invalid measurement data (NaN or zero at start) for range {range_idx}. Skipping correction."
            )
            continue

        # Get section boundaries (using 0-based Python indexing)
        start_idx = cal_range["hex_start_idx"]  # Config uses 1-based for clarity
        end_idx = cal_range["hex_end_idx"] + 1  # Python slice excludes end
        num_points_in_range = end_idx - start_idx
        points_to_modify = cal_range["points_to_modify"]

        if len(measured_amps) != num_points_in_range:
            print(
                f" Warning: Mismatch between measurement points ({len(measured_amps)}) and expected hex range points ({num_points_in_range}) for range {range_idx}. Skipping."
            )
            continue

        # Extract the relevant section from the *original* calibration data
        original_section = original_cal_data[start_idx:end_idx]

        # --- Calculate Correction Factors ---
        # Normalize measured response relative to the first point in the range
        relative_response = measured_amps / measured_amps[0]

        # Avoid division by zero if relative_response has zeros (shouldn't happen if checked above)
        relative_response[relative_response == 0] = (
            1e-9  # Replace zeros with small number
        )

        # New calibration factor = Original Factor / Measured Relative Response
        # If measured output dropped (relative_response < 1), new factor > original factor.
        # If measured output peaked (relative_response > 1), new factor < original factor.
        new_cal_section = original_section / relative_response
        # --- Apply Correction to the specified points ---
        # Determine indices *within the section* to modify (last 'points_to_modify')
        modify_start_in_section = num_points_in_range - points_to_modify
        modify_end_in_section = num_points_in_range

        # Determine indices *within the full modified_cal_data array*
        modify_start_global = start_idx + modify_start_in_section
        modify_end_global = start_idx + modify_end_in_section

        print(
            f"  Modifying indices {modify_start_global} to {modify_end_global - 1} (total {points_to_modify} points)"
        )

        # Update the modified data array only for the selected points
        modified_cal_data[modify_start_global:modify_end_global] = new_cal_section[
            modify_start_in_section:modify_end_in_section
        ]

        # --- Plotting for verification ---
        plot_indices = np.arange(start_idx, end_idx)
        plt.plot(
            plot_indices,
            original_section,
            "--",
            label=f"Orig Range {range_idx} (Idx {start_idx}-{end_idx - 1})",
        )
        plt.plot(
            plot_indices, new_cal_section, "-", label=f"New Calc Range {range_idx}"
        )
        # Highlight modified points
        plt.scatter(
            plot_indices[modify_start_in_section:modify_end_in_section],
            new_cal_section[modify_start_in_section:modify_end_in_section],
            color="red",
            s=20,
            zorder=5,
            label=f"Modified Pts Rng {range_idx}",
        )

    # Add overall plot elements
    plt.title(f"Calibration Factors - {os.path.basename(output_hex_path)}")
    plt.xlabel("Index in .hex file")
    plt.ylabel("Calibration Factor")
    plt.legend(fontsize="small")
    plt.grid(True)
    plt.tight_layout()
    plot_filename = os.path.splitext(output_hex_path)[0] + "_comparison.png"
    plt.savefig(plot_filename)
    print(f"Saved comparison plot to {plot_filename}")
    plt.show()

    # 3. Write the modified calibration data
    try:
        with open(output_hex_path, "wb") as fh:
            modified_cal_data.tofile(fh)
        print(
            f"Successfully wrote {len(modified_cal_data)} points to {output_hex_path}"
        )
        return True
    except Exception as e:
        print(f"Error writing modified file {output_hex_path}: {e}")
        return False

## 3. Connect to Instruments

In [ ]:
gen, osc = connect_instruments(GEN_IP, OSC_IP)

# Proceed only if connection is successful
if gen is None or osc is None:
    print(
        "\nERROR: Instrument connection failed. Please check IPs, connections, and VISA setup."
    )
    # Optionally raise an error: raise ConnectionError("Failed to connect to instruments")
else:
    print("\nInstruments connected successfully.")

## 4. Perform Measurements
This section iterates through the specified channels and calibration ranges, performing measurements for each.

In [ ]:
all_channel_measurements = {}  # Dictionary to store results {channel: {range_idx: data}}

if gen and osc:  # Only run if instruments are connected
    for channel in CHANNELS_TO_CALIBRATE:
        print(f"\n--- Starting Measurements for Channel {channel} ---")
        channel_measurements = {}  # Store results for this channel {range_idx: data}

        for i, cal_range in enumerate(CAL_RANGES):
            range_idx = i + 1  # 1-based index
            voltage_vpp = cal_range["voltage"]
            # Convert frequencies from uHz to Hz for measurement
            frequencies_hz = cal_range["frequencies_uHz"] / 1e6

            # Perform the measurement
            measured_freqs_hz, measured_amps_rms = measure_flatness(
                gen, osc, channel, voltage_vpp, frequencies_hz, OSC_MEAS_CMD
            )

            # Store results
            measurement_data = {
                "frequencies_hz": measured_freqs_hz,
                "measured_amps_rms": measured_amps_rms,
                "voltage_vpp": voltage_vpp,
                "channel": channel,
                "range_idx": range_idx,
            }
            channel_measurements[range_idx] = measurement_data

            # Save intermediate results for this range
            filename = MEASUREMENT_FILE_TEMPLATE.format(
                channel=channel, range_idx=range_idx
            )
            filepath = os.path.join(DATA_DIR, filename)
            try:
                np.savez(filepath, **measurement_data)
                print(f"Saved measurement data to: {filepath}")
            except Exception as e:
                print(f"Error saving measurement data to {filepath}: {e}")

            print("-" * 20)  # Separator between ranges

        all_channel_measurements[channel] = channel_measurements
        print(f"--- Finished Measurements for Channel {channel} ---")

else:
    print("\nSkipping measurements due to connection failure.")

## 5. Calculate New Calibration and Generate .hex Files
This section processes the measurement data saved in step 4 and generates the modified `.hex` files.

In [ ]:
if all_channel_measurements:  # Proceed only if measurements were taken
    for channel in CHANNELS_TO_CALIBRATE:
        print(f"\n--- Calculating Calibration for Channel {channel} ---")

        original_hex_path = os.path.join(DATA_DIR, ORIGINAL_HEX_FILES[channel])
        output_hex_path = os.path.join(DATA_DIR, MODIFIED_HEX_FILES[channel])
        measurements_for_channel = all_channel_measurements.get(channel)

        if not measurements_for_channel:
            print(
                f"Error: No measurement data found for Channel {channel}. Skipping calculation."
            )
            continue

        success = calculate_and_update_cal(
            original_hex_path,
            measurements_for_channel,
            CAL_RANGES,
            HEX_DATA_TYPE,
            output_hex_path,
        )

        if success:
            print(
                f"Successfully generated modified calibration file for Channel {channel}."
            )
        else:
            print(
                f"Failed to generate modified calibration file for Channel {channel}."
            )

else:
    print(
        "\nSkipping calibration calculation because no measurements were performed or loaded."
    )

## 6. Visualize Original vs. Modified Calibration Data (Optional)
Plot the original and newly generated `_mod.hex` files together for comparison.

In [ ]:
print("\n--- Plotting Final Comparison ---")
plt.figure(figsize=(12, 7))

file_labels = []

# Plot original files
for ch in CHANNELS_TO_CALIBRATE:
    fname = os.path.join(DATA_DIR, ORIGINAL_HEX_FILES[ch])
    try:
        with open(fname, "rb") as fh:
            data = np.fromfile(fh, dtype=HEX_DATA_TYPE)
        plt.plot(data, "--", label=f"Original CH{ch}")
        file_labels.append(f"Orig CH{ch}")
    except FileNotFoundError:
        print(f"Warning: Original file not found for plotting: {fname}")
    except Exception as e:
        print(f"Error reading {fname} for plotting: {e}")

# Plot modified files
for ch in CHANNELS_TO_CALIBRATE:
    fname = os.path.join(DATA_DIR, MODIFIED_HEX_FILES[ch])
    try:
        with open(fname, "rb") as fh:
            data = np.fromfile(fh, dtype=HEX_DATA_TYPE)
        plt.plot(data, "-", linewidth=2, label=f"Modified CH{ch}")
        file_labels.append(f"Mod CH{ch}")
    except FileNotFoundError:
        print(f"Warning: Modified file not found for plotting: {fname}")
    except Exception as e:
        print(f"Error reading {fname} for plotting: {e}")

# Add vertical lines indicating range boundaries (using 0-based index)
# Boundaries are *after* the end index of a range
boundaries = sorted(list(set([r["hex_end_idx"] for r in CAL_RANGES])))
if boundaries:
    plt.vlines(
        boundaries[:-1],
        ymin=plt.ylim()[0],
        ymax=plt.ylim()[1],
        colors="r",
        linestyles=":",
        label="Range Boundary",
    )
    # file_labels.append('Boundary') # Optional: add to legend

plt.title("Comparison of Original and Modified HF Flatness Calibration Data")
plt.xlabel("Index in .hex file")
plt.ylabel("Calibration Factor")
plt.legend()
plt.grid(True)
plt.tight_layout()
plt.show()

## 7. Upload Calibration Files to Generator using ADB

In [ ]:
print("\n--- ADB Upload Commands ---")
print("Run these commands in your system terminal (cmd, bash, etc.):")
print("# Connect to the device (if not already connected):")
print(f"adb connect {ADB_DEVICE_ID}")
print("-" * 20)

for ch in CHANNELS_TO_CALIBRATE:
    mod_file_local = os.path.join(DATA_DIR, MODIFIED_HEX_FILES[ch])
    original_filename_remote = ORIGINAL_HEX_FILES[
        ch
    ]  # Overwrite the original name on device
    # Assuming the standard Rigol path, adjust if necessary
    remote_path = f"/rigol/data/{original_filename_remote}"

    # Important: Ensure paths are correctly quoted if they contain spaces
    # Using pathlib helps create OS-agnostic paths for the local file
    mod_file_local_str = str(pathlib.Path(mod_file_local))

    print(f"# Upload Channel {ch}:")
    # Use quotes around paths, especially the local one if it might have spaces
    print(f'adb -s {ADB_DEVICE_ID} push "{mod_file_local_str}" "{remote_path}"')
    print("")  # Add a newline for clarity

print("--- End of ADB Commands ---")
print(
    "\nAfter uploading, it is recommended to REBOOT the signal generator for the new calibration data to take effect."
)

In [ ]:
if gen:
    gen.close()
    print("Generator connection closed.")
if osc:
    osc.close()
    print("Oscilloscope connection closed.")

print("\nCalibration process finished.")